# Input Source Codes

In [1]:
import os
import re
import nltk
import pandas as pd
import numpy as np
nltk.download('punkt')

from nltk.tokenize import word_tokenize
from sklearn.metrics import accuracy_score,precision_score,recall_score,f1_score

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\haydariday\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
source_codes = []
filenames = []
LOC = []
n_LOC = []
filenames_without_extension = []


tags_count = {}
function_dict = {}
function_token = {}

stop_condition = ('for', 'if', 'else', 'while','switch')

tags_count['LOC'] = 0
tags_count['SLOC'] = 0
tags_count['O'] = 0
tags_count['C'] = 0
tags_count['M'] = 0
tags_count['N'] = 0


sc_directory = 'Source_codes/postgre/'
py_directory = 'postgre.xls'

In [3]:
%%time

filenames = os.listdir(sc_directory)
for name in filenames :
    i = name.replace('.c','')
    filenames_without_extension.append(i)
filenames

Wall time: 0 ns


['list.c', 'outfuncs.c', 'pqformat.c', 'readfuncs.c', 'value.c']

In [4]:
%%time
i = 0
for files in filenames :
    function_dict[filenames_without_extension[i]] = {}
    with open(sc_directory+files,'r') as fh :
        source_codes.append([filenames_without_extension[i],fh.readlines()])
    i += 1

Wall time: 2 ms


In [5]:
%%time

for source_code in source_codes :
    i = 0
    for baris in source_code :
        if not (i % 2 == 0) :
            LOC.append(len(baris))
            tags_count['LOC'] += len(baris)
        i+=1
LOC

Wall time: 0 ns


[1275, 2820, 708, 1350, 75]

In [6]:
tags_count['LOC']

6228

In [8]:
%%time
for code in source_codes :
    lines_update = []
    for i in range(1,len(code[1])+1) :
        lines_update.append([i,code[1][i-1]])
    code[1] = lines_update

Wall time: 2 ms


# Data Pre-Processing 

## Remove whitespace

In [10]:
%%time
for code in source_codes :
    for i in range(len(code[1])) :
        code[1][i][1] = ' '.join(code[1][i][1].split())
        code[1][i][1] = code[1][i][1].replace('\t', '')
        code[1][i][1] = code[1][i][1].replace('\n', '')
        code[1][i][1] = code[1][i][1].replace('\\n\\', '')
        code[1][i][1] = code[1][i][1].replace('\\n', '')
        code[1][i][1] = code[1][i][1].replace('\\', ' \\ ')
        code[1][i][1] = code[1][i][1].replace('/', ' / ')
        code[1][i][1] = code[1][i][1].replace('\'', ' \' ')
        code[1][i][1] = code[1][i][1].replace('"', ' " ')
        code[1][i][1] = re.sub(r"^\s+","",code[1][i][1])

Wall time: 26 ms


## Split Codes

In [12]:
%%time
for source_code in source_codes :
    i = 0
    for baris in source_code[1] :
        if not (baris[1] == '') :
            baris[1] = word_tokenize(baris[1])
        i += 1

Wall time: 432 ms


## Remove Comments

### Tag Comments

In [14]:
%%time
petik = 0
for source_code in source_codes :
    is_comment = False
    is_comment_line = False
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            tag = 'O'
            tags_count['O'] += 1
            #print(source_code[1][baris_index][1][word_index],end=' ')
            if not(is_comment or is_comment_line) : 
                out_of_bound = (len(source_code[1][baris_index][1])-word_index <= 1)
                #print('o',end=' ')
                if not(out_of_bound) :
                    #print('baris :',baris_index)
                    if (source_code[1][baris_index][1][word_index] == '/') and (source_code[1][baris_index][1][word_index+1] == '*') :
                        petik = 0
                        for indexes in range(word_index) :
                            #print(source_code[1][baris_index][1][indexes][0])
                            if (source_code[1][baris_index][1][indexes][0] == "``" or source_code[1][baris_index][1][indexes][0] == "'" or source_code[1][baris_index][1][indexes][0] == '"') :
                                petik += 1
                        #print(petik)
                        if (petik == 0 or petik%2 == 0) :
                            is_comment = True
                            tag = 'C'
                            tags_count['O'] -= 1
                        #print('yes1',end=' ')
                    elif (source_code[1][baris_index][1][word_index] == '/') and (source_code[1][baris_index][1][word_index+1] == '/') :
                        is_comment_line = True
                        tag = 'C'
                        tags_count['O'] -= 1
                        #print('yes2',end=' ')
            elif (is_comment or is_comment_line) :
                tag = 'C'
                tags_count['O'] -= 1
                #print('yes3',end=' ')
                if (word_index > 0) and (is_comment) :
                    #print('no1',end=' ')
                    #print(source_code[1][baris_index][1][word_index-1], source_code[1][baris_index][1][word_index])
                    if (source_code[1][baris_index][1][word_index-1][0] == '*') and (source_code[1][baris_index][1][word_index] == '/') :
                        #print('no2',end=' ')
                        if (word_index > 1) :
                            #print('no3',end=' ')
                            if not (source_code[1][baris_index][1][word_index-2][0] == '/') :
                                is_comment = False
                                #print('no',end=' ')
                        else :
                            is_comment = False
            source_code[1][baris_index][1][word_index] = [source_code[1][baris_index][1][word_index], tag]
            word_index += 1
            #print('oh')
        baris_index += 1
        is_comment_line = False

#
endif
return
NIL
;
return
NIL
;
nskip
=
0
;
#
endif
if
(
p
!
=
str
)
if
(
p
!
=
str
)
if
(
p
!
=
str
)
#
else
if
(
p
!
=
str
)
result
=
0
;
#
else
if
(
p
!
=
str
)
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
local_node-
>
fldname
=
-1
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
local_node-
>
catalogname
=
NULL
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_strtok
(
&
length
)
;
token
=
pg_st

### Removing Comments

In [16]:
%%time

for source_code in source_codes :
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            if (source_code[1][baris_index][1][word_index][1] == 'C') :
                source_code[1][baris_index][1].pop(word_index)
                tags_count['C'] += 1
            else :
                word_index += 1
        baris_index += 1

Wall time: 19 ms


## Remove Empty Baris

In [17]:
%%time

for source_code in source_codes :
    baris_index = 0   
    while (baris_index < len(source_code[1])) :
        if len(source_code[1][baris_index][1]) <= 0 :
            source_code[1].pop(baris_index)
        else :
            baris_index += 1
    n_LOC.append(len(source_code[1]))
    tags_count['SLOC'] += len(source_code[1])

Wall time: 3 ms


In [18]:
n_LOC

[738, 2254, 373, 873, 34]

In [19]:
tags_count['SLOC']

4272

# Tag Function

In [21]:
def check_is_function(source_code, index_word, index_baris, dict_function) :
    found = False #awali dengan kondisi tidak ditemukan
    
    #kondisi ketika pointer '{' merupakan urutan awal dari barisan token
    if (index_word <= 0) :
        try :
            index_baris = index_baris - 1
            index_word = len(source_code[1][index_baris][1]) - 1
        except :
            print("something went wrong, pointer can't get back to previous line")
    
    #kondisi ketika pointer '{' bukan urutan awal dari barisan
    else :
        index_word -=  1
        
    #kondisi ketika tidak menemukan token ')'
    #print('1.5',source_code[1][index_baris][1][index_word][0])
    if (not(source_code[1][index_baris][1][index_word][0] == ')')) :
        #print('why0')
        return False
    
    #cek apakah pointer berada pada baris awal dari source code
    if not(index_baris<=0) :
        #cek apakah pointer ada didalam macro
        if (source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0]=='\\') :
            #print('why1')
            return False
    if (source_code[1][index_baris][1][0][0]=='#') :
        #print('why2')
        return False
    
    while (index_baris >= 0 and not(found)) :
        while (index_word >= 0 and not(found)) :
            #print('2',source_code[1][index_baris][1][index_word][0])
            if (source_code[1][index_baris][1][index_word][0] in stop_condition) :
                #print('why3')
                return False
            elif (source_code[1][index_baris][1][index_word][0] in (';','}')) :
                found = True;
            else :
                index_word -= 1
        if not(found) :
            index_baris = index_baris - 1
            index_word  = len(source_code[1][index_baris][1]) - 1
            
            # cek apakah baris macro
            #print('3',source_code[1][index_baris][1][index_word][0])
            if not(index_baris<=0) :
            #cek apakah pointer ada didalam macro
                #print('4',source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0])
                if (source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1])-1][0]=='\\') :
                    found = True
            if (source_code[1][index_baris][1][0][0]=='#') :
                found = True

    if (len(source_code[1][index_baris][1]) - index_word <= 1 ) :
        index_baris += 1
        index_word = 0
    else :
        index_word += 1
        
    count = 0
    count_on = False
    is_named = False
    lines = []
    function_name = ''
    file_name = ''
    
    while (index_baris < len(source_code[1]) and (count>0 or not count_on)) :
        index_word = 0
        lines_temp = []
        lines_temp.append(source_code[1][index_baris][0])
        while (index_word < len(source_code[1][index_baris][1]) and (count>0 or not count_on)) :
            #print('g',source_code[1][index_baris][1][index_word])
            #print(index_baris)
            source_code[1][index_baris][1][index_word][1] = 'M'
            tags_count['M'] += 1
            tags_count['O'] -= 1
            lines_temp.append(source_code[1][index_baris][1][index_word][0])
            if (source_code[1][index_baris][1][index_word][0] == '{') :
                #print('yes0')
                count_on = True
                count += 1
            elif (not(is_named) and source_code[1][index_baris][1][index_word][0] == '(') :
                #print('yes1')
                if (index_word <= 0) :
                    #print('yes2')
                    source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1]) - 1][1] = 'N'
                    tags_count['M'] -= 1
                    tags_count['N'] += 1
                    function_name = source_code[1][index_baris-1][1][len(source_code[1][index_baris-1][1]) - 1][0]
                else :
                    #print('yes3')
                    source_code[1][index_baris][1][index_word-1][1] = 'N'
                    tags_count['M'] -= 1
                    tags_count['N'] += 1
                    function_name = source_code[1][index_baris][1][index_word-1][0]
                file_name = source_code[0]
                dict_function[file_name.lower()][function_name.lower()] = {}
                is_named = True
            elif (source_code[1][index_baris][1][index_word][0] == '}') :
                #print('yes4')
                count -= 1
            if (count>0 or not(count_on)) :
                index_word += 1
            #print(index_word < len(source_code[1][index_baris][1]) and (count>0 or not count_on))
        #print('final')
        lines.append(lines_temp)
        if (count>0 or not(count_on)) :
            index_baris += 1
    dict_function[file_name.lower()][function_name.lower()]['code'] = {}
    for line in lines :
        dict_function[file_name.lower()][function_name.lower()]['code'][line[0]] = []
        index = 1
        while (index<len(line)) :
            dict_function[file_name.lower()][function_name.lower()]['code'][line[0]].append(line[index])
            index += 1
    return True

In [22]:
%%time
jumlah = 0

for source_code in source_codes :
    baris_index = 0
    while (baris_index < len(source_code[1])) :
        word_index = 0
        while (word_index < len(source_code[1][baris_index][1])) :
            #print(baris_index,word_index)
            if not(source_code[1][baris_index][1][word_index][1] in ('M','N')) :    
                if (source_code[1][baris_index][1][word_index][0] == '{') :
                    if (check_is_function(source_code, word_index, baris_index,function_dict)) :
                        jumlah += 1
            word_index += 1
        baris_index += 1
#print('Jumlah :',jumlah)

Wall time: 65 ms


In [23]:
tags_count['M']

20759

In [24]:
tags_count['N']

290

In [25]:
tags_count['O']

1122

In [26]:
tags_count['C']

9115

In [27]:
tags_count['all'] = tags_count['M'] + tags_count['N'] + tags_count['O'] + tags_count['C']
tags_count['all']

31286

# Tokenization

In [29]:
syntax = ('for', 'while', 'case', 'if', 'do', 'else', 'break', 'continue', 'switch', 'goto', 'return')

def give_token(x) : 
    if x == 'for' :
        return 'A'
    elif x == 'break' :
        return 'B'
    elif x == 'case' :
        return 'C'
    elif x == 'do' :
        return 'D'
    elif x == 'else' :
        return 'E'
    elif x == 'continue' :
        return 'F'
    elif x == 'goto' :
        return 'G'
    elif x == 'while' :
        return 'H'
    elif x == 'if' :
        return 'I'
    elif x == 'switch' :
        return 'J'
    elif x == 'return' :
        return 'K'
    else :
        return False

In [30]:
%%time

is_in_comment1 = False
is_in_comment2 = False
is_in_comment3 = False
is_comment = False
dummy = {}
for file in list(function_dict) :
    dummy[file] = {}
    for function in list(function_dict[file]) :
        dummy[file][function] = {}
        dummy[file][function]['token'] = ''
        #print(function)
        for baris in list(function_dict[file][function]['code']) :
            for token in list(function_dict[file][function]['code'][baris]) :
                #print(token)
                if (token == '"' and not(is_in_comment2) and not(is_in_comment3)) :
                    #print('comment1')
                    if not(is_in_comment1) :
                        dummy[file][function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment1 = not(is_in_comment1)
                elif (token == "'" and not(is_in_comment1) and not(is_in_comment3)) :
                    #print('comment2')
                    if not(is_in_comment2) : 
                        dummy[file][function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment2 = not(is_in_comment2)
                elif ((token == "``" or token == "''") and not(is_in_comment1) and not(is_in_comment2)) :
                    #print('comment3')
                    if not(is_in_comment3) :
                        dummy[file][function]['token'] += 'T'
                        is_comment = not(is_comment)
                    is_in_comment3 = not(is_in_comment3)
                if (not(is_in_comment1 or is_in_comment2 or is_in_comment3 or is_comment)) :
                    if (re.search(r'^-[\w._]+$',token)) :
                        #print('1',re.findall(r'^-[\w._]+$',token)[0])
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            dummy[file][function]['token'] += '-'
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[file][function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[file][function]['token'] += 'T'
                    elif (re.search(r'^[\w._]+[^\w._]+$',token)) :
                        #print('2',re.findall(r'^[\w._]+[^\w._]+$',token)[0])
                        if (re.findall(r'^[\w._]+',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+',token)[0]))
                            dummy[file][function]['token'] += give_token(re.findall(r'^[\w._]+',token)[0])
                        else :
                            dummy[file][function]['token'] += 'T'
                        dummy[file][function]['token'] += re.findall(r'[^\w._]+$',token)[0]
                    elif (re.search(r'^[^\w._]+[\w._]+$',token)) :
                        #print('3',re.findall(r'^[^\w._]+[\w._]+$',token)[0])
                        dummy[file][function]['token'] += re.findall(r'^[^\w._]+',token)[0]
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[file][function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[file][function]['token'] += 'T'
                    elif(re.search(r'^[\w.]+[^\w.]+[\w.]+$',token)) :
                        #print('4',re.findall(r'^[\w.]+[^\w.]+[\w.]+$',token)[0])
                        if (re.findall(r'^[\w._]+',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+',token)[0]))
                            dummy[file][function]['token'] += give_token(re.findall(r'^[\w._]+',token)[0])
                        else :
                            dummy[file][function]['token'] += 'T'
                        dummy[file][function]['token'] += re.findall(r'[^\w._]+',token)[0]
                        if (re.findall(r'[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'[\w._]+$',token)[0]))
                            dummy[file][function]['token'] += give_token(re.findall(r'[\w._]+$',token)[0])
                        else :
                            dummy[file][function]['token'] += 'T'
                    elif (re.search(r'^[\w._]+$',token)) :
                        #print('5',re.findall(r'^[\w._]+$',token)[0])
                        if (re.findall(r'^[\w._]+$',token)[0] in syntax) :
                            if not (give_token(re.findall(r'^[\w._]+$',token)[0])) :
                                raise Exception('"{}" not found!'.format(re.findall(r'^[\w._]+$',token)[0]))
                            dummy[file][function]['token'] += give_token(re.findall(r'^[\w._]+$',token)[0])
                        else :
                            #print('why :',re.findall(r'^[\w._]+$',token)[0])
                            dummy[file][function]['token'] += 'T'
                    else :
                        dummy[file][function]['token'] += token
                elif (not(is_in_comment1 or is_in_comment2 or is_in_comment3)) :
                    #print('NO')
                    is_comment = not(is_comment)
                    
for file in list(function_dict) :
    for function in list(function_dict[file]) :
        function_dict[file][function]['token'] = dummy[file][function]['token']

Wall time: 115 ms


In [33]:
i = 0
for file in function_dict :
    for function in function_dict[file] :
        function_token[file+'..'+function+'()']= function_dict[file][function]['token']

# Matching

In [34]:
import textdistance as td

## Compare Functions

In [35]:
for file in function_dict :
    for function in function_dict[file] :
        print(file,function,function_dict[file][function]['token'])

list check_list_invariants TTT(T*T){I(T==T)K;T(T->T>T);T(T->T!=T);T(T->T!=T);T(T->T==T||T->T==T||T->T==T);I(T->T==T)T(T->T==T->T);I(T->T==T)T(T->T->T==T->T);T(T->T->T==T);}
list new_list TT*T(TT){T*T;T*T;T=(T*)T(T(*T));T->T=T;T=(T*)T(T(*T));T->T=T;T->T=T;T->T=T;T->T=T;KT;}
list new_head_cell TTT(T*T){T*T;T=(T*)T(T(*T));T->T=T->T;T->T=T;T->T++;}
list new_tail_cell TTT(T*T){T*T;T=(T*)T(T(*T));T->T=T;T->T->T=T;T->T=T;T->T++;}
list lappend T*T(T*T,T*T){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}
list lappend_int T*T(T*T,TT){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}
list lappend_oid T*T(T*T,TT){T(T(T));I(T==T)T=T(T);ET(T);T(T->T)=T;T(T);KT;}
list add_new_cell TT*T(T*T,T*T){T*T;T=(T*)T(T(*T));T->T=T->T;T->T=T;I(T->T==T)T->T=T;T->T++;KT;}
list lappend_cell T*T(T*T,T*T,T*T){T*T;T(T(T));T=T(T,T);T(T)=T;T(T);KT;}
list lappend_cell_int T*T(T*T,T*T,TT){T*T;T(T(T));T=T(T,T);T(T)=T;T(T);KT;}
list lappend_cell_oid T*T(T*T,T*T,TT){T*T;T(T(T));T=T(T,T);T(T)=T;T(T);KT;}
list lcons T*T(T*T,T*T)

### ratcliff_obershelp

In [36]:
%%time
i = 0
key = list(function_token)
dummy = {}
is_clone10 = []
is_clone20 = []
is_clone30 = []
is_clone40 = []
is_clone50 = []
is_clone60 = []
is_clone70 = []
is_clone80 = []
is_clone90 = []
is_clone100 = []
while i < len(function_token)-1 :
    j = i+1
    while j < len(function_token) :
        if (key[i]<=key[j]) :
            func_to_compare = key[i]+'-'+key[j]
        else :
            func_to_compare = key[j]+'-'+key[i]
        dummy[func_to_compare] = td.ratcliff_obershelp(function_token[key[i]],function_token[key[j]])
        is_clone10.append(True)
        is_clone20.append(True)
        is_clone30.append(True)
        is_clone40.append(True)
        is_clone50.append(True)
        is_clone60.append(True)
        is_clone70.append(True)
        is_clone80.append(True)
        is_clone90.append(True)
        is_clone100.append(True)
        if (dummy[func_to_compare] < 1) :
            is_clone100[-1] = False
        if (dummy[func_to_compare] < 0.9) :
            is_clone90[-1] = False
        if (dummy[func_to_compare] < 0.8) :
            is_clone80[-1] = False
        if (dummy[func_to_compare] < 0.7) :
            is_clone70[-1] = False
        if (dummy[func_to_compare] < 0.6) :
            is_clone60[-1] = False
        if (dummy[func_to_compare] < 0.5) :
            is_clone50[-1] = False    
        if (dummy[func_to_compare] < 0.4) :
            is_clone40[-1] = False
        if (dummy[func_to_compare] < 0.3) :
            is_clone30[-1] = False
        if (dummy[func_to_compare] < 0.2) :
            is_clone20[-1] = False
        if (dummy[func_to_compare] < 0.1) :
            is_clone10[-1] = False
        j += 1
    i += 1

Wall time: 37.1 s


# Format Output

In [37]:

df = pd.DataFrame(data=dummy.items(),columns=['Method','Ratio'])
df['>10%'] = pd.DataFrame(is_clone10)
df['>20%'] = pd.DataFrame(is_clone20)
df['>30%'] = pd.DataFrame(is_clone30)
df['>40%'] = pd.DataFrame(is_clone40)
df['>50%'] = pd.DataFrame(is_clone50)
df['>60%'] = pd.DataFrame(is_clone60)
df['>70%'] = pd.DataFrame(is_clone70)
df['>80%'] = pd.DataFrame(is_clone80)
df['>90%'] = pd.DataFrame(is_clone90)
df['>100%'] = pd.DataFrame(is_clone100)

#df.set_index(['Method'], inplace=True)
df

Method     Ratio  >10%  \
0         list..check_list_invariants()-list..new_list()  0.389610  True   
1      list..check_list_invariants()-list..new_head_c...  0.373737  True   
2      list..check_list_invariants()-list..new_tail_c...  0.429268  True   
3          list..check_list_invariants()-list..lappend()  0.380488  True   
4      list..check_list_invariants()-list..lappend_int()  0.382353  True   
...                                                  ...       ...   ...   
41900           value..makeinteger()-value..makestring()  0.985915  True   
41901        value..makebitstring()-value..makeinteger()  0.985915  True   
41902             value..makefloat()-value..makestring()  1.000000  True   
41903          value..makebitstring()-value..makefloat()  1.000000  True   
41904         value..makebitstring()-value..makestring()  1.000000  True   

       >20%  >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
0      True  True  False  False  False  False  False  False  False  
1      True  True  False  False  False  False  False  False  False  
2      True  True   True  False  False  False  False  False  False  
3      True  True  False  False  False  False  False  False  False  
4      True  True  False  False  False  False  False  False  False  
...     ...   ...    ...    ...    ...    ...    ...    ...    ...  
41900  True  True   True   True   True   True   True   True  False  
41901  True  True   True   True   True   True   True   True  False  
41902  True  True   True   True   True   True   True   True   True  
41903  True  True   True   True   True   True   True   True   True  
41904  True  True   True   True   True   True   True   True   True  

[41905 rows x 12 columns]

In [38]:
df.sort_values(['Ratio'], ascending=False, axis=0, inplace=True)
df

Method     Ratio   >10%  \
41904         value..makebitstring()-value..makestring()  1.000000   True   
17385  outfuncs.._outbitmapand()-outfuncs.._outworkta...  1.000000   True   
17380  outfuncs.._outbitmapand()-outfuncs.._outtidscan()  1.000000   True   
33685  outfuncs.._outinnerindexscaninfo()-outfuncs.._...  1.000000   True   
40590  readfuncs.._readarrayref()-readfuncs.._readwin...  1.000000   True   
...                                                  ...       ...    ...   
12900             list..list_free()-outfuncs.._outnode()  0.017467  False   
14325           list..list_length()-outfuncs.._outnode()  0.016349  False   
14090             list..list_tail()-outfuncs.._outnode()  0.016340  False   
13854             list..list_head()-outfuncs.._outnode()  0.016340  False   
14559                list..length()-outfuncs.._outnode()  0.015292  False   

        >20%   >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
41904   True   True   True   True   True   True   True   True   True  
17385   True   True   True   True   True   True   True   True   True  
17380   True   True   True   True   True   True   True   True   True  
33685   True   True   True   True   True   True   True   True   True  
40590   True   True   True   True   True   True   True   True   True  
...      ...    ...    ...    ...    ...    ...    ...    ...    ...  
12900  False  False  False  False  False  False  False  False  False  
14325  False  False  False  False  False  False  False  False  False  
14090  False  False  False  False  False  False  False  False  False  
13854  False  False  False  False  False  False  False  False  False  
14559  False  False  False  False  False  False  False  False  False  

[41905 rows x 12 columns]

In [39]:
df['Method']=df['Method'].str.lower()
df

Method     Ratio   >10%  \
41904         value..makebitstring()-value..makestring()  1.000000   True   
17385  outfuncs.._outbitmapand()-outfuncs.._outworkta...  1.000000   True   
17380  outfuncs.._outbitmapand()-outfuncs.._outtidscan()  1.000000   True   
33685  outfuncs.._outinnerindexscaninfo()-outfuncs.._...  1.000000   True   
40590  readfuncs.._readarrayref()-readfuncs.._readwin...  1.000000   True   
...                                                  ...       ...    ...   
12900             list..list_free()-outfuncs.._outnode()  0.017467  False   
14325           list..list_length()-outfuncs.._outnode()  0.016349  False   
14090             list..list_tail()-outfuncs.._outnode()  0.016340  False   
13854             list..list_head()-outfuncs.._outnode()  0.016340  False   
14559                list..length()-outfuncs.._outnode()  0.015292  False   

        >20%   >30%   >40%   >50%   >60%   >70%   >80%   >90%  >100%  
41904   True   True   True   True   True   True   True   True   True  
17385   True   True   True   True   True   True   True   True   True  
17380   True   True   True   True   True   True   True   True   True  
33685   True   True   True   True   True   True   True   True   True  
40590   True   True   True   True   True   True   True   True   True  
...      ...    ...    ...    ...    ...    ...    ...    ...    ...  
12900  False  False  False  False  False  False  False  False  False  
14325  False  False  False  False  False  False  False  False  False  
14090  False  False  False  False  False  False  False  False  False  
13854  False  False  False  False  False  False  False  False  False  
14559  False  False  False  False  False  False  False  False  False  

[41905 rows x 12 columns]

# Comparison

In [40]:
df_py = pd.read_excel(py_directory)
df_py

Unnamed: 0  Unnamed: 1  Student  \
0      outfuncs.._outjoinpathinfo()-outfuncs.._outbit...         NaN      0.0   
1      outfuncs.._outaggref()-outfuncs.._outbitmaphea...         NaN      NaN   
2      outfuncs.._outaggref()-outfuncs.._outjoinpathi...         NaN      NaN   
3      outfuncs.._outvaluesscan()-outfuncs.._outbitma...         NaN      NaN   
4      outfuncs.._outvaluesscan()-outfuncs.._outjoinp...         NaN      NaN   
...                                                  ...         ...      ...   
41333                                                NaN         NaN      NaN   
41334                                                NaN         NaN      NaN   
41335                                                NaN         NaN      NaN   
41336                                                NaN         NaN      NaN   
41337                                                NaN         NaN      NaN   

      Unnamed: 3    Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
0            NaN  No Clone       0.0       0.0       0.0         0.0   
1            NaN       NaN       0.0       0.0       0.0         0.0   
2            NaN       NaN       0.0       0.0       0.0         0.0   
3            NaN       NaN       0.0       0.0       0.0         0.0   
4            NaN       NaN       0.0       0.0       0.0         0.0   
...          ...       ...       ...       ...       ...         ...   
41333     Type 1         0       NaN       NaN       NaN         NaN   
41334     Type 2        18       NaN       NaN       NaN         NaN   
41335     Type 3        10       NaN       NaN       NaN         NaN   
41336     Type 4         5       NaN       NaN       NaN         NaN   
41337   No Clone       601       NaN       NaN       NaN         NaN   

       MeCC_95_10  ...  MeCC_70_20  MeCC_70_10  MeCC_70_4  MeCC_60_20  \
0             0.0  ...         0.0         0.0        0.0         0.0   
1             0.0  ...         0.0         0.0        0.0         0.0   
2             0.0  ...         0.0         0.0        0.0         0.0   
3             0.0  ...         0.0         0.0        0.0         0.0   
4             0.0  ...         0.0         0.0        0.0         0.0   
...           ...  ...         ...         ...        ...         ...   
41333         NaN  ...         NaN         NaN        NaN         NaN   
41334         NaN  ...         NaN         NaN        NaN         NaN   
41335         NaN  ...         NaN         NaN        NaN         NaN   
41336         NaN  ...         NaN         NaN        NaN         NaN   
41337         NaN  ...         NaN         NaN        NaN         NaN   

       MeCC_60_10  MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  Simcad  
0             0.0        0.0         0.0         0.0        0.0     0.0  
1             0.0        0.0         0.0         0.0        0.0     0.0  
2             0.0        0.0         0.0         0.0        0.0     0.0  
3             0.0        0.0         0.0         0.0        0.0     0.0  
4             0.0        0.0         0.0         0.0        0.0     0.0  
...           ...        ...         ...         ...        ...     ...  
41333         NaN        NaN         NaN         NaN        NaN     NaN  
41334         NaN        NaN         NaN         NaN        NaN     NaN  
41335         NaN        NaN         NaN         NaN        NaN     NaN  
41336         NaN        NaN         NaN         NaN        NaN     NaN  
41337         NaN        NaN         NaN         NaN        NaN     NaN  

[41338 rows x 27 columns]

In [41]:
df_py = df_py.dropna(subset=['Expert', 'Student'])
df_py = df_py.rename(columns={'Unnamed: 0': 'Method'})
df_py

Method  Unnamed: 1  Student  \
0      outfuncs.._outjoinpathinfo()-outfuncs.._outbit...         NaN     0.00   
63      outfuncs.._outcreatestmt()-outfuncs.._outlimit()         NaN     0.25   
126    list..list_concat_unique()-readfuncs.._readsor...         NaN     0.00   
198    readfuncs.._readtargetentry()-outfuncs.._outli...         NaN     0.00   
261     readfuncs.._readrangevar()-outfuncs.._outlimit()         NaN     0.00   
...                                                  ...         ...      ...   
40509  readfuncs.._readscalararrayopexpr()-readfuncs....         NaN     0.75   
40572  readfuncs.._readscalararrayopexpr()-outfuncs.....         NaN     0.00   
40698  readfuncs.._readscalararrayopexpr()-outfuncs.....         NaN     0.75   
40986  outfuncs.._outrowcompareexpr()-outfuncs.._outa...         NaN     0.25   
41226   list..list_append_unique()-outfuncs.._outaexpr()         NaN     0.00   

      Unnamed: 3    Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
0            NaN  No Clone       0.0       0.0       0.0         0.0   
63           NaN  No Clone       0.0       0.0       0.0         0.0   
126          NaN  No Clone       0.0       0.0       0.0         0.0   
198          NaN  No Clone       0.0       0.0       0.0         0.0   
261          NaN  No Clone       0.0       0.0       0.0         0.0   
...          ...       ...       ...       ...       ...         ...   
40509        NaN    Type 3       0.0       0.0       0.0         0.0   
40572        NaN  No Clone       0.0       0.0       0.0         0.0   
40698        NaN  No Clone       0.0       0.0       0.0         0.0   
40986        NaN  No Clone       0.0       0.0       0.0         0.0   
41226        NaN  No Clone       0.0       0.0       0.0         0.0   

       MeCC_95_10  ...  MeCC_70_20  MeCC_70_10  MeCC_70_4  MeCC_60_20  \
0             0.0  ...         0.0         0.0        0.0         0.0   
63            0.0  ...         0.0         0.0        0.0         0.0   
126           0.0  ...         0.0         0.0        0.0         0.0   
198           0.0  ...         0.0         0.0        0.0         0.0   
261           0.0  ...         0.0         0.0        0.0         0.0   
...           ...  ...         ...         ...        ...         ...   
40509         0.0  ...         0.0         0.0        0.0         0.0   
40572         0.0  ...         0.0         0.0        0.0         0.0   
40698         0.0  ...         0.0         0.0        0.0         0.0   
40986         0.0  ...         0.0         0.0        0.0         0.0   
41226         0.0  ...         0.0         0.0        0.0         0.0   

       MeCC_60_10  MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  Simcad  
0             0.0        0.0         0.0         0.0        0.0     0.0  
63            0.0        0.0         0.0         0.0        0.0     0.0  
126           0.0        0.0         0.0         0.0        0.0     0.0  
198           0.0        0.0         0.0         0.0        0.0     0.0  
261           0.0        0.0         0.0         0.0        0.0     0.0  
...           ...        ...         ...         ...        ...     ...  
40509         0.0        0.0         0.0         0.0        0.0     0.0  
40572         0.0        0.0         0.0         0.0        0.0     0.0  
40698         0.0        0.0         0.0         0.0        0.0     0.0  
40986         0.0        0.0         0.0         0.0        0.0     0.0  
41226         0.0        0.0         0.0         0.0        0.0     0.0  

[657 rows x 27 columns]

In [42]:
df_py['Expert'].unique()

array(['No Clone', 'Unsure', 'Type 2', 'Type 3', 'Type 4', 'type 4',
       'Not Classified', 'type 2'], dtype=object)

In [43]:
df_py = df_py[df_py.Expert != 'Unsure']
df_py = df_py[df_py.Expert != 'Not Classified']
df_py = df_py[df_py.Expert != 15]
df_py = df_py[df_py.Expert != 18]
df_py

Method  Unnamed: 1  Student  \
0      outfuncs.._outjoinpathinfo()-outfuncs.._outbit...         NaN     0.00   
63      outfuncs.._outcreatestmt()-outfuncs.._outlimit()         NaN     0.25   
126    list..list_concat_unique()-readfuncs.._readsor...         NaN     0.00   
198    readfuncs.._readtargetentry()-outfuncs.._outli...         NaN     0.00   
261     readfuncs.._readrangevar()-outfuncs.._outlimit()         NaN     0.00   
...                                                  ...         ...      ...   
40509  readfuncs.._readscalararrayopexpr()-readfuncs....         NaN     0.75   
40572  readfuncs.._readscalararrayopexpr()-outfuncs.....         NaN     0.00   
40698  readfuncs.._readscalararrayopexpr()-outfuncs.....         NaN     0.75   
40986  outfuncs.._outrowcompareexpr()-outfuncs.._outa...         NaN     0.25   
41226   list..list_append_unique()-outfuncs.._outaexpr()         NaN     0.00   

      Unnamed: 3    Expert  Nicad-30  Nicad-40  Nicad-50  MeCC_95_20  \
0            NaN  No Clone       0.0       0.0       0.0         0.0   
63           NaN  No Clone       0.0       0.0       0.0         0.0   
126          NaN  No Clone       0.0       0.0       0.0         0.0   
198          NaN  No Clone       0.0       0.0       0.0         0.0   
261          NaN  No Clone       0.0       0.0       0.0         0.0   
...          ...       ...       ...       ...       ...         ...   
40509        NaN    Type 3       0.0       0.0       0.0         0.0   
40572        NaN  No Clone       0.0       0.0       0.0         0.0   
40698        NaN  No Clone       0.0       0.0       0.0         0.0   
40986        NaN  No Clone       0.0       0.0       0.0         0.0   
41226        NaN  No Clone       0.0       0.0       0.0         0.0   

       MeCC_95_10  ...  MeCC_70_20  MeCC_70_10  MeCC_70_4  MeCC_60_20  \
0             0.0  ...         0.0         0.0        0.0         0.0   
63            0.0  ...         0.0         0.0        0.0         0.0   
126           0.0  ...         0.0         0.0        0.0         0.0   
198           0.0  ...         0.0         0.0        0.0         0.0   
261           0.0  ...         0.0         0.0        0.0         0.0   
...           ...  ...         ...         ...        ...         ...   
40509         0.0  ...         0.0         0.0        0.0         0.0   
40572         0.0  ...         0.0         0.0        0.0         0.0   
40698         0.0  ...         0.0         0.0        0.0         0.0   
40986         0.0  ...         0.0         0.0        0.0         0.0   
41226         0.0  ...         0.0         0.0        0.0         0.0   

       MeCC_60_10  MeCC_60_4  MeCC_50_20  MeCC_50_10  MeCC_50_4  Simcad  
0             0.0        0.0         0.0         0.0        0.0     0.0  
63            0.0        0.0         0.0         0.0        0.0     0.0  
126           0.0        0.0         0.0         0.0        0.0     0.0  
198           0.0        0.0         0.0         0.0        0.0     0.0  
261           0.0        0.0         0.0         0.0        0.0     0.0  
...           ...        ...         ...         ...        ...     ...  
40509         0.0        0.0         0.0         0.0        0.0     0.0  
40572         0.0        0.0         0.0         0.0        0.0     0.0  
40698         0.0        0.0         0.0         0.0        0.0     0.0  
40986         0.0        0.0         0.0         0.0        0.0     0.0  
41226         0.0        0.0         0.0         0.0        0.0     0.0  

[634 rows x 27 columns]

In [44]:
df_py = df_py.rename(columns={'Unnamed: 0':'Method'})

In [45]:
df_lain = df_py.drop(['Unnamed: 1','Unnamed: 3'],axis=1)
df_lain.to_excel('df_lain.xlsx')

In [46]:
df.to_excel('df_py.xlsx')

In [47]:
df_py = df_py[['Method','Expert']]
df_py

Method    Expert
0      outfuncs.._outjoinpathinfo()-outfuncs.._outbit...  No Clone
63      outfuncs.._outcreatestmt()-outfuncs.._outlimit()  No Clone
126    list..list_concat_unique()-readfuncs.._readsor...  No Clone
198    readfuncs.._readtargetentry()-outfuncs.._outli...  No Clone
261     readfuncs.._readrangevar()-outfuncs.._outlimit()  No Clone
...                                                  ...       ...
40509  readfuncs.._readscalararrayopexpr()-readfuncs....    Type 3
40572  readfuncs.._readscalararrayopexpr()-outfuncs.....  No Clone
40698  readfuncs.._readscalararrayopexpr()-outfuncs.....  No Clone
40986  outfuncs.._outrowcompareexpr()-outfuncs.._outa...  No Clone
41226   list..list_append_unique()-outfuncs.._outaexpr()  No Clone

[634 rows x 2 columns]

### Check if both result detected same methods

In [48]:
arr_comparable_methods = list(df_py['Method'])

arr_temp = []
for comparable_methods in arr_comparable_methods :
    temp = sorted(comparable_methods.split('-'))
    #print(temp)
    arr_temp.append(temp)
arr_comparable_methods = arr_temp

['outfuncs.._outbitmapheapscan()', 'outfuncs.._outjoinpathinfo()']
['outfuncs.._outcreatestmt()', 'outfuncs.._outlimit()']
['list..list_concat_unique()', 'readfuncs.._readsortgroupclause()']
['outfuncs.._outlimit()', 'readfuncs.._readtargetentry()']
['outfuncs.._outlimit()', 'readfuncs.._readrangevar()']
['outfuncs.._outcasetestexpr()', 'outfuncs.._outsortgroupclause()']
['list..list_concat_unique_ptr()', 'readfuncs.._readquery()']
['readfuncs.._readfuncexpr()', 'readfuncs.._readquery()']
['pqformat..pq_copymsgbytes()', 'readfuncs.._readquery()']
['readfuncs.._readaggref()', 'readfuncs.._readwindowfunc()']
['list..list_delete()', 'outfuncs.._outlimit()']
['outfuncs.._outrowexpr()', 'readfuncs.._readjoinexpr()']
['list..lappend_int()', 'pqformat..pq_sendcountedtext()']
['pqformat..pq_sendcountedtext()', 'readfuncs.._readnullifexpr()']
['list..list_delete_first()', 'outfuncs.._outcasetestexpr()']
['outfuncs.._outnulltest()', 'outfuncs.._outsortgroupclause()']
['outfuncs.._outcasewhen()',

In [49]:
list0 = []
for row,col in df.iterrows() :
    methods = df.at[row,'Method'].split('-')
    for method in methods :
        #print(method)
        if (method.lower() in list0) :
            #print('no')
        else :
            list0.append(method.lower())
            #print('yes')

value..makebitstring()
yes
value..makestring()
yes
outfuncs.._outbitmapand()
yes
outfuncs.._outworktablescan()
yes
outfuncs.._outbitmapand()
no
outfuncs.._outtidscan()
yes
outfuncs.._outinnerindexscaninfo()
yes
outfuncs.._outrestarget()
yes
readfuncs.._readarrayref()
yes
readfuncs.._readwindowclause()
yes
readfuncs.._readwindowclause()
no
readfuncs.._readwindowfunc()
yes
readfuncs.._readaggref()
yes
readfuncs.._readwindowclause()
no
outfuncs.._outcoerceviaio()
yes
outfuncs.._outconvertrowtypeexpr()
yes
outfuncs.._outbitmapand()
no
outfuncs.._outvaluesscan()
yes
outfuncs.._outplaceholdervar()
yes
outfuncs.._outsortgroupclause()
yes
outfuncs.._outnullifexpr()
yes
outfuncs.._outwindowdef()
yes
outfuncs.._outbitmapand()
no
outfuncs.._outhashjoin()
yes
readfuncs.._readfieldstore()
yes
readfuncs.._readsortgroupclause()
yes
readfuncs.._readfieldselect()
yes
readfuncs.._readsortgroupclause()
no
outfuncs.._outplaceholdervar()
no
outfuncs.._outrestarget()
no
readfuncs.._readcurrentofexpr()
yes
r

In [50]:
list1 = []
for comparable_methods in arr_comparable_methods :
    for method in comparable_methods :
        #print(method)
        if (method.lower() in list1) :
            #print('no')
        else :
            list1.append(method.lower())
            #print('yes')

outfuncs.._outbitmapheapscan()
yes
outfuncs.._outjoinpathinfo()
yes
outfuncs.._outcreatestmt()
yes
outfuncs.._outlimit()
yes
list..list_concat_unique()
yes
readfuncs.._readsortgroupclause()
yes
outfuncs.._outlimit()
no
readfuncs.._readtargetentry()
yes
outfuncs.._outlimit()
no
readfuncs.._readrangevar()
yes
outfuncs.._outcasetestexpr()
yes
outfuncs.._outsortgroupclause()
yes
list..list_concat_unique_ptr()
yes
readfuncs.._readquery()
yes
readfuncs.._readfuncexpr()
yes
readfuncs.._readquery()
no
pqformat..pq_copymsgbytes()
yes
readfuncs.._readquery()
no
readfuncs.._readaggref()
yes
readfuncs.._readwindowfunc()
yes
list..list_delete()
yes
outfuncs.._outlimit()
no
outfuncs.._outrowexpr()
yes
readfuncs.._readjoinexpr()
yes
list..lappend_int()
yes
pqformat..pq_sendcountedtext()
yes
pqformat..pq_sendcountedtext()
no
readfuncs.._readnullifexpr()
yes
list..list_delete_first()
yes
outfuncs.._outcasetestexpr()
no
outfuncs.._outnulltest()
yes
outfuncs.._outsortgroupclause()
no
outfuncs.._outcasewh

#### Check if there are any differences

In [51]:
set(list1).issubset(set(list0))

True

In [52]:
set(list0).difference(set(list1))

{'list..check_list_invariants()',
 'list..lcons()',
 'list..list_concat()',
 'list..list_difference_oid()',
 'list..list_head()',
 'list..list_member_int()',
 'list..list_tail()',
 'list..list_union()',
 'outfuncs.._outa_indices()',
 'outfuncs.._outaggref()',
 'outfuncs.._outbitmapindexscan()',
 'outfuncs.._outboolexpr()',
 'outfuncs.._outcoalesceexpr()',
 'outfuncs.._outcolumnref()',
 'outfuncs.._outctescan()',
 'outfuncs.._outfuncexpr()',
 'outfuncs.._outjoin()',
 'outfuncs.._outmaterial()',
 'outfuncs.._outparamref()',
 'outfuncs.._outplannerparamitem()',
 'outfuncs.._outrestarget()',
 'outfuncs.._outselectstmt()',
 'outfuncs.._outtidscan()',
 'outfuncs.._outuniquepath()',
 'pqformat..pq_beginmessage()',
 'pqformat..pq_getmsgtext()',
 'readfuncs.._readarraycoerceexpr()',
 'readfuncs.._readcommontableexpr()',
 'readfuncs.._readintoclause()',
 'readfuncs.._readnulltest()',
 'readfuncs.._readrangetblref()',
 'readfuncs.._readrowexpr()',
 'readfuncs.._readrowmarkclause()',
 'readfuncs..

#### Get all the comparable method

In [53]:
for row in df_py['Method'] :
    key=row.split('-')
    if (key[0]<=key[1]) :
        new_key = key[0]+'-'+key[1]
    else :        
        new_key = key[1]+'-'+key[0]
        #print(new_key+" df_py")
    df_py=df_py.replace(to_replace=row, value=new_key)
    
for row in df['Method'] :
    key=row.split('-')
    if (key[0]<=key[1]) :
        new_key = key[0]+'-'+key[1]
    else :
        new_key = key[1]+'-'+key[0]
        #print(new_key+" df")
    df=df.replace(to_replace=row, value=new_key)

outfuncs.._outbitmapheapscan()-outfuncs.._outjoinpathinfo() df_py
outfuncs.._outlimit()-readfuncs.._readtargetentry() df_py
outfuncs.._outlimit()-readfuncs.._readrangevar() df_py
outfuncs.._outcasetestexpr()-outfuncs.._outsortgroupclause() df_py
list..list_concat_unique_ptr()-readfuncs.._readquery() df_py
readfuncs.._readfuncexpr()-readfuncs.._readquery() df_py
readfuncs.._readaggref()-readfuncs.._readwindowfunc() df_py
list..lappend_int()-pqformat..pq_sendcountedtext() df_py
pqformat..pq_sendcountedtext()-readfuncs.._readnullifexpr() df_py
outfuncs.._outlimit()-pqformat..pq_sendbyte() df_py
outfuncs.._outdefelem()-outfuncs.._outfromexpr() df_py
list..list_delete_first()-outfuncs.._outappendrelinfo() df_py
list..list_nth()-value..makefloat() df_py
outfuncs.._outbitmapheapscan()-outfuncs.._outsubqueryscan() df_py
outfuncs.._outbitmapheapscan()-outfuncs.._outindexscan() df_py
outfuncs.._outinhrelation()-pqformat..pq_endmessage() df_py
list..list_nth()-outfuncs.._outvar() df_py
pqformat..

In [54]:
df_py=df_py.set_index('Method')
df_py

Expert
Method                                                      
outfuncs.._outbitmapheapscan()-outfuncs.._outjo...  No Clone
outfuncs.._outcreatestmt()-outfuncs.._outlimit()    No Clone
list..list_concat_unique()-readfuncs.._readsort...  No Clone
outfuncs.._outlimit()-readfuncs.._readtargetent...  No Clone
outfuncs.._outlimit()-readfuncs.._readrangevar()    No Clone
...                                                      ...
readfuncs.._readscalararrayopexpr()-readfuncs.....    Type 3
outfuncs.._outa_arrayexpr()-readfuncs.._readsca...  No Clone
outfuncs.._outbitmapandpath()-readfuncs.._reads...  No Clone
outfuncs.._outarrayexpr()-outfuncs.._outrowcomp...  No Clone
list..list_append_unique()-outfuncs.._outaexpr()    No Clone

[634 rows x 1 columns]

In [55]:
df.to_excel('df_py.xlsx')

In [56]:
df = df.set_index('Method')
df

Ratio   >10%   >20%  \
Method                                                                       
value..makebitstring()-value..makestring()          1.000000   True   True   
outfuncs.._outbitmapand()-outfuncs.._outworktab...  1.000000   True   True   
outfuncs.._outbitmapand()-outfuncs.._outtidscan()   1.000000   True   True   
outfuncs.._outinnerindexscaninfo()-outfuncs.._o...  1.000000   True   True   
readfuncs.._readarrayref()-readfuncs.._readwind...  1.000000   True   True   
...                                                      ...    ...    ...   
list..list_free()-outfuncs.._outnode()              0.017467  False  False   
list..list_length()-outfuncs.._outnode()            0.016349  False  False   
list..list_tail()-outfuncs.._outnode()              0.016340  False  False   
list..list_head()-outfuncs.._outnode()              0.016340  False  False   
list..length()-outfuncs.._outnode()                 0.015292  False  False   

                                                     >30%   >40%   >50%  \
Method                                                                    
value..makebitstring()-value..makestring()           True   True   True   
outfuncs.._outbitmapand()-outfuncs.._outworktab...   True   True   True   
outfuncs.._outbitmapand()-outfuncs.._outtidscan()    True   True   True   
outfuncs.._outinnerindexscaninfo()-outfuncs.._o...   True   True   True   
readfuncs.._readarrayref()-readfuncs.._readwind...   True   True   True   
...                                                   ...    ...    ...   
list..list_free()-outfuncs.._outnode()              False  False  False   
list..list_length()-outfuncs.._outnode()            False  False  False   
list..list_tail()-outfuncs.._outnode()              False  False  False   
list..list_head()-outfuncs.._outnode()              False  False  False   
list..length()-outfuncs.._outnode()                 False  False  False   

                                                     >60%   >70%   >80%  \
Method                                                                    
value..makebitstring()-value..makestring()           True   True   True   
outfuncs.._outbitmapand()-outfuncs.._outworktab...   True   True   True   
outfuncs.._outbitmapand()-outfuncs.._outtidscan()    True   True   True   
outfuncs.._outinnerindexscaninfo()-outfuncs.._o...   True   True   True   
readfuncs.._readarrayref()-readfuncs.._readwind...   True   True   True   
...                                                   ...    ...    ...   
list..list_free()-outfuncs.._outnode()              False  False  False   
list..list_length()-outfuncs.._outnode()            False  False  False   
list..list_tail()-outfuncs.._outnode()              False  False  False   
list..list_head()-outfuncs.._outnode()              False  False  False   
list..length()-outfuncs.._outnode()                 False  False  False   

                                                     >90%  >100%  
Method                                                            
value..makebitstring()-value..makestring()           True   True  
outfuncs.._outbitmapand()-outfuncs.._outworktab...   True   True  
outfuncs.._outbitmapand()-outfuncs.._outtidscan()    True   True  
outfuncs.._outinnerindexscaninfo()-outfuncs.._o...   True   True  
readfuncs.._readarrayref()-readfuncs.._readwind...   True   True  
...                                                   ...    ...  
list..list_free()-outfuncs.._outnode()              False  False  
list..list_length()-outfuncs.._outnode()            False  False  
list..list_tail()-outfuncs.._outnode()              False  False  
list..list_head()-outfuncs.._outnode()              False  False  
list..length()-outfuncs.._outnode()                 False  False  

[41905 rows x 11 columns]

In [57]:
df.to_excel('df.xlsx')

In [58]:
df_final=pd.concat([df, df_py], axis=1)
df_final = df_final.dropna(subset=['Expert'])
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^No Clone$', value= False, regex=True)
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^Type.*$', value= True, regex=True)
df_final['Expert'] = df_final['Expert'].replace(to_replace=r'^type.*$', value= True, regex=True)

In [59]:
df_final

Ratio   >10%   >20%  \
outfuncs.._outfieldselect()-outfuncs.._outinner...  1.000000   True   True   
outfuncs.._outbitmapor()-outfuncs.._outresultpa...  1.000000   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...  1.000000   True   True   
readfuncs.._readaggref()-readfuncs.._readwindow...  1.000000   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outrange...  1.000000   True   True   
...                                                      ...    ...    ...   
list..list_copy_tail()-outfuncs.._outnullifexpr()   0.185484   True  False   
list..list_copy_tail()-outfuncs.._outopexpr()       0.185484   True  False   
list..list_copy()-list..list_free()                 0.170455   True  False   
list..list_copy_tail()-outfuncs.._outplan()         0.113537   True  False   
outfuncs.._outnode()-outfuncs.._outtypecast()       0.031368  False  False   

                                                     >30%   >40%   >50%  \
outfuncs.._outfieldselect()-outfuncs.._outinner...   True   True   True   
outfuncs.._outbitmapor()-outfuncs.._outresultpa...   True   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...   True   True   True   
readfuncs.._readaggref()-readfuncs.._readwindow...   True   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outrange...   True   True   True   
...                                                   ...    ...    ...   
list..list_copy_tail()-outfuncs.._outnullifexpr()   False  False  False   
list..list_copy_tail()-outfuncs.._outopexpr()       False  False  False   
list..list_copy()-list..list_free()                 False  False  False   
list..list_copy_tail()-outfuncs.._outplan()         False  False  False   
outfuncs.._outnode()-outfuncs.._outtypecast()       False  False  False   

                                                     >60%   >70%   >80%  \
outfuncs.._outfieldselect()-outfuncs.._outinner...   True   True   True   
outfuncs.._outbitmapor()-outfuncs.._outresultpa...   True   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...   True   True   True   
readfuncs.._readaggref()-readfuncs.._readwindow...   True   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outrange...   True   True   True   
...                                                   ...    ...    ...   
list..list_copy_tail()-outfuncs.._outnullifexpr()   False  False  False   
list..list_copy_tail()-outfuncs.._outopexpr()       False  False  False   
list..list_copy()-list..list_free()                 False  False  False   
list..list_copy_tail()-outfuncs.._outplan()         False  False  False   
outfuncs.._outnode()-outfuncs.._outtypecast()       False  False  False   

                                                     >90%  >100%  Expert  
outfuncs.._outfieldselect()-outfuncs.._outinner...   True   True   False  
outfuncs.._outbitmapor()-outfuncs.._outresultpa...   True   True    True  
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...   True   True    True  
readfuncs.._readaggref()-readfuncs.._readwindow...   True   True    True  
outfuncs.._outa_arrayexpr()-outfuncs.._outrange...   True   True    True  
...                                                   ...    ...     ...  
list..list_copy_tail()-outfuncs.._outnullifexpr()   False  False   False  
list..list_copy_tail()-outfuncs.._outopexpr()       False  False   False  
list..list_copy()-list..list_free()                 False  False   False  
list..list_copy_tail()-outfuncs.._outplan()         False  False   False  
outfuncs.._outnode()-outfuncs.._outtypecast()       False  False   False  

[634 rows x 12 columns]

In [60]:
for ratio in ['>10%','>20%','>30%','>40%','>50%','>60%','>70%','>80%','>90%','>100%'] :
    comparison_column = np.where((df_final[ratio] == df_final['Expert']) , True, False)
    df_final[ratio+' Result'] = comparison_column

In [61]:
df_final

Ratio   >10%   >20%  \
outfuncs.._outfieldselect()-outfuncs.._outinner...  1.000000   True   True   
outfuncs.._outbitmapor()-outfuncs.._outresultpa...  1.000000   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...  1.000000   True   True   
readfuncs.._readaggref()-readfuncs.._readwindow...  1.000000   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outrange...  1.000000   True   True   
...                                                      ...    ...    ...   
list..list_copy_tail()-outfuncs.._outnullifexpr()   0.185484   True  False   
list..list_copy_tail()-outfuncs.._outopexpr()       0.185484   True  False   
list..list_copy()-list..list_free()                 0.170455   True  False   
list..list_copy_tail()-outfuncs.._outplan()         0.113537   True  False   
outfuncs.._outnode()-outfuncs.._outtypecast()       0.031368  False  False   

                                                     >30%   >40%   >50%  \
outfuncs.._outfieldselect()-outfuncs.._outinner...   True   True   True   
outfuncs.._outbitmapor()-outfuncs.._outresultpa...   True   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...   True   True   True   
readfuncs.._readaggref()-readfuncs.._readwindow...   True   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outrange...   True   True   True   
...                                                   ...    ...    ...   
list..list_copy_tail()-outfuncs.._outnullifexpr()   False  False  False   
list..list_copy_tail()-outfuncs.._outopexpr()       False  False  False   
list..list_copy()-list..list_free()                 False  False  False   
list..list_copy_tail()-outfuncs.._outplan()         False  False  False   
outfuncs.._outnode()-outfuncs.._outtypecast()       False  False  False   

                                                     >60%   >70%   >80%  \
outfuncs.._outfieldselect()-outfuncs.._outinner...   True   True   True   
outfuncs.._outbitmapor()-outfuncs.._outresultpa...   True   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...   True   True   True   
readfuncs.._readaggref()-readfuncs.._readwindow...   True   True   True   
outfuncs.._outa_arrayexpr()-outfuncs.._outrange...   True   True   True   
...                                                   ...    ...    ...   
list..list_copy_tail()-outfuncs.._outnullifexpr()   False  False  False   
list..list_copy_tail()-outfuncs.._outopexpr()       False  False  False   
list..list_copy()-list..list_free()                 False  False  False   
list..list_copy_tail()-outfuncs.._outplan()         False  False  False   
outfuncs.._outnode()-outfuncs.._outtypecast()       False  False  False   

                                                     >90%  ...  >10% Result  \
outfuncs.._outfieldselect()-outfuncs.._outinner...   True  ...        False   
outfuncs.._outbitmapor()-outfuncs.._outresultpa...   True  ...         True   
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...   True  ...         True   
readfuncs.._readaggref()-readfuncs.._readwindow...   True  ...         True   
outfuncs.._outa_arrayexpr()-outfuncs.._outrange...   True  ...         True   
...                                                   ...  ...          ...   
list..list_copy_tail()-outfuncs.._outnullifexpr()   False  ...        False   
list..list_copy_tail()-outfuncs.._outopexpr()       False  ...        False   
list..list_copy()-list..list_free()                 False  ...        False   
list..list_copy_tail()-outfuncs.._outplan()         False  ...        False   
outfuncs.._outnode()-outfuncs.._outtypecast()       False  ...         True   

                                                    >20% Result  >30% Result  \
outfuncs.._outfieldselect()-outfuncs.._outinner...        False        False   
outfuncs.._outbitmapor()-outfuncs.._outresultpa...         True         True   
outfuncs.._outa_arrayexpr()-outfuncs.._outcaset...         True         True   
readfuncs.._readaggref()-readfuncs.._readwindow

In [62]:
df_final.to_excel("output.xlsx") 

In [63]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>10%'], rownames=['Actual'], colnames=['Predicted'])
print(">10% Accuracy :",accuracy_score(df_final['Expert'],df_final['>10%']))
print(">10% Precision :",precision_score(df_final['Expert'],df_final['>10%']))
print(">10% Recall :",recall_score(df_final['Expert'],df_final['>10%']))
print(">10% F1 :",f1_score(df_final['Expert'],df_final['>10%']))
confusion_matrix

>10% Accuracy : 0.05362776025236593
>10% Precision : 0.052132701421800945
>10% Recall : 1.0
>10% F1 : 0.0990990990990991


Predicted  False  True 
Actual                 
False          1    600
True           0     33

In [64]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>20%'], rownames=['Actual'], colnames=['Predicted'])
print(">20% Accuracy :",accuracy_score(df_final['Expert'],df_final['>20%']))
print(">20% Precision :",precision_score(df_final['Expert'],df_final['>20%']))
print(">20% Recall :",recall_score(df_final['Expert'],df_final['>20%']))
print(">20% F1 :",f1_score(df_final['Expert'],df_final['>20%']))
confusion_matrix

>20% Accuracy : 0.06624605678233439
>20% Precision : 0.0528
>20% Recall : 1.0
>20% F1 : 0.10030395136778116


Predicted  False  True 
Actual                 
False          9    592
True           0     33

In [65]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>30%'], rownames=['Actual'], colnames=['Predicted'])
print(">30% Accuracy :",accuracy_score(df_final['Expert'],df_final['>30%']))
print(">30% Precision :",precision_score(df_final['Expert'],df_final['>30%']))
print(">30% Recall :",recall_score(df_final['Expert'],df_final['>30%']))
print(">30% F1 :",f1_score(df_final['Expert'],df_final['>30%']))
confusion_matrix

>30% Accuracy : 0.138801261829653
>30% Precision : 0.05699481865284974
>30% Recall : 1.0
>30% F1 : 0.10784313725490197


Predicted  False  True 
Actual                 
False         55    546
True           0     33

In [66]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>40%'], rownames=['Actual'], colnames=['Predicted'])
print(">40% Accuracy :",accuracy_score(df_final['Expert'],df_final['>40%']))
print(">40% Precision :",precision_score(df_final['Expert'],df_final['>40%']))
print(">40% Recall :",recall_score(df_final['Expert'],df_final['>40%']))
print(">40% F1 :",f1_score(df_final['Expert'],df_final['>40%']))
confusion_matrix

>40% Accuracy : 0.23659305993690852
>40% Precision : 0.06382978723404255
>40% Recall : 1.0
>40% F1 : 0.12


Predicted  False  True 
Actual                 
False        117    484
True           0     33

In [67]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>50%'], rownames=['Actual'], colnames=['Predicted'])
print(">50% Accuracy :",accuracy_score(df_final['Expert'],df_final['>50%']))
print(">50% Precision :",precision_score(df_final['Expert'],df_final['>50%']))
print(">50% Recall :",recall_score(df_final['Expert'],df_final['>50%']))
print(">50% F1 :",f1_score(df_final['Expert'],df_final['>50%']))
confusion_matrix

>50% Accuracy : 0.43217665615141954
>50% Precision : 0.08396946564885496
>50% Recall : 1.0
>50% F1 : 0.15492957746478872


Predicted  False  True 
Actual                 
False        241    360
True           0     33

In [68]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>60%'], rownames=['Actual'], colnames=['Predicted'])
print(">60% Accuracy :",accuracy_score(df_final['Expert'],df_final['>60%']))
print(">60% Precision :",precision_score(df_final['Expert'],df_final['>60%']))
print(">60% Recall :",recall_score(df_final['Expert'],df_final['>60%']))
print(">60% F1 :",f1_score(df_final['Expert'],df_final['>60%']))
confusion_matrix

>60% Accuracy : 0.637223974763407
>60% Precision : 0.12547528517110265
>60% Recall : 1.0
>60% F1 : 0.22297297297297294


Predicted  False  True 
Actual                 
False        371    230
True           0     33

In [69]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>70%'], rownames=['Actual'], colnames=['Predicted'])
print(">70% Accuracy :",accuracy_score(df_final['Expert'],df_final['>70%']))
print(">70% Precision :",precision_score(df_final['Expert'],df_final['>70%']))
print(">70% Recall :",recall_score(df_final['Expert'],df_final['>70%']))
print(">70% F1 :",f1_score(df_final['Expert'],df_final['>70%']))
confusion_matrix

>70% Accuracy : 0.7839116719242902
>70% Precision : 0.19411764705882353
>70% Recall : 1.0
>70% F1 : 0.3251231527093596


Predicted  False  True 
Actual                 
False        464    137
True           0     33

In [70]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>80%'], rownames=['Actual'], colnames=['Predicted'])
print(">80% Accuracy :",accuracy_score(df_final['Expert'],df_final['>80%']))
print(">80% Precision :",precision_score(df_final['Expert'],df_final['>80%']))
print(">80% Recall :",recall_score(df_final['Expert'],df_final['>80%']))
print(">80% F1 :",f1_score(df_final['Expert'],df_final['>80%']))
confusion_matrix

>80% Accuracy : 0.8911671924290221
>80% Precision : 0.3235294117647059
>80% Recall : 1.0
>80% F1 : 0.48888888888888893


Predicted  False  True 
Actual                 
False        532     69
True           0     33

In [71]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>90%'], rownames=['Actual'], colnames=['Predicted'])
print(">90% Accuracy :",accuracy_score(df_final['Expert'],df_final['>90%']))
print(">90% Precision :",precision_score(df_final['Expert'],df_final['>90%']))
print(">90% Recall :",recall_score(df_final['Expert'],df_final['>90%']))
print(">90% F1 :",f1_score(df_final['Expert'],df_final['>90%']))
confusion_matrix

>90% Accuracy : 0.9511041009463722
>90% Precision : 0.5277777777777778
>90% Recall : 0.5757575757575758
>90% F1 : 0.5507246376811594


Predicted  False  True 
Actual                 
False        584     17
True          14     19

In [72]:
confusion_matrix = pd.crosstab(df_final['Expert'], df_final['>100%'], rownames=['Actual'], colnames=['Predicted'])
print(">100% Accuracy :",accuracy_score(df_final['Expert'],df_final['>100%']))
print(">100% Precision :",precision_score(df_final['Expert'],df_final['>100%']))
print(">100% Recall :",recall_score(df_final['Expert'],df_final['>100%']))
print(">100% F1 :",f1_score(df_final['Expert'],df_final['>100%']))
confusion_matrix

>100% Accuracy : 0.9574132492113565
>100% Precision : 0.8
>100% Recall : 0.24242424242424243
>100% F1 : 0.372093023255814


Predicted  False  True 
Actual                 
False        599      2
True          25      8